In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import netCDF4 as nc
from datetime import datetime
import scipy.io as sio
import datetime
from datetime import datetime, timedelta
import matplotlib.colors as mcolors
import matplotlib.ticker as ticker
import matplotlib.animation
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

ssh_path = '/srv/scratch/z5297792/IN2023/IMOS_aggregation.nc'
ssh_dataset = nc.Dataset(ssh_path, mode='r')
lon_ssh, lat_ssh = ssh_dataset['LONGITUDE'][:].data, ssh_dataset['LATITUDE'][:].data
lon_ssh, lat_ssh = np.meshgrid(lon_ssh, lat_ssh)
u_ssh, v_ssh = ssh_dataset['UCUR'][:].data, ssh_dataset['VCUR'][:].data # TIME, LATITUDE, LONGITUDE
u_ssh, v_ssh = np.transpose(u_ssh, axes=(2,1,0)), np.transpose(v_ssh, axes=(2,1,0)) # LON, LAT, TIME
tim_ssh = ssh_dataset['TIME'][:].data # days since 1985-01-01 00:00:00 UTC

ref_date = pd.Timestamp("1985-01-01 00:00:00")
tim_ssh = ref_date + pd.to_timedelta(tim_ssh, unit="D")

tim_ssh = tim_ssh[tim_ssh<= pd.Timestamp('2023-12-10 06:00:00')]

In [8]:
df_CE2_ssh_trace = pd.read_pickle("Drifter_plot_data/df_CE2_ssh_trace.pkl")
df_CE2_espra = pd.read_pickle("Drifter_plot_data/df_CE2_espra.pkl")
df_CE2_analysis = pd.read_pickle("Drifter_plot_data/df_CE2_analysis.pkl")

lon_min_CE2, lon_max_CE2 = 153, 155
lat_min_CE2, lat_max_CE2 = -38.75, -37

In [22]:
df_CE2_analysis

Lon        Lat         u         v                       Time  \
0     154.357059 -37.005208  0.534412 -0.052615 2023-10-17 10:27:31.000004   
1     154.360804 -37.038123  0.533096 -0.055888 2023-10-17 10:42:30.333327   
2     154.364625 -37.071899  0.431565 -0.059157 2023-10-17 10:57:30.666685   
3     154.368274 -37.101418  0.368063  0.005275 2023-10-17 11:12:30.333340   
4     154.372221 -37.104340  0.357789  0.053638 2023-10-17 11:27:30.666659   
...          ...        ...       ...       ...                        ...   
3587  153.013885 -37.499874 -0.152935  0.215966 2023-12-10 05:00:00.000000   
3588  153.119049 -37.663380 -0.524762  0.072178 2023-12-10 05:00:00.000000   
3589  153.006195 -37.492554 -0.218226  0.222258 2023-12-10 06:00:00.000000   
3590  153.096695 -37.660057 -0.557605  0.125522 2023-12-10 06:00:00.000000   
3591  153.426163 -37.128307  0.578315 -0.123444 2023-12-10 06:00:00.000000   

        ID  
0      NaN  
1      NaN  
2      NaN  
3      NaN  
4      NaN  
...    ...  
3587  12.0  
3588  13.0  
3589  12.0  
3590  13.0  
3591  16.0  

[3592 rows x 6 columns]

In [3]:
def plot_ellipse(Q, center=(0, 0), scale=1):
    def normalize_matrix(A, norm_type='fro'):
        norm = np.linalg.norm(A, 'fro') if norm_type == 'fro' else np.max(np.abs(A))
        return A / norm if norm else A
    Q = normalize_matrix(Q)

    def swap_principal_axes(Q):
        eigvals, eigvecs = np.linalg.eigh(Q)
        return eigvecs @ np.diag(eigvals[::-1]) @ eigvecs.T

    Q = swap_principal_axes(Q)
    
    eigenvalues, eigenvectors = np.linalg.eigh(Q)
    if np.any(eigenvalues < 0):

        Q = np.array([[np.abs(Q[0,0]), Q[0,1]], [Q[1,0], np.abs(Q[1,1])]])

        def flip_Q_y(Q):
            F_y = np.diag([-1, 1])
            return F_y.T @ Q @ F_y

        Q = flip_Q_y(Q)

        eigenvalues, eigenvectors = np.linalg.eigh(Q)
        if np.any(eigenvalues < 0):
            return np.nan, np.nan
    a, b = np.sqrt(eigenvalues) * scale
    theta = np.arctan2(eigenvectors[1, 0], eigenvectors[0, 0])
    t = np.linspace(0, 2 * np.pi, 100)
    x, y = a * np.cos(t), b * np.sin(t)
    R = np.array([[np.cos(theta), -np.sin(theta)], [np.sin(theta), np.cos(theta)]])
    x_ellipse, y_ellipse = R @ np.array([x, y]) + np.array(center).reshape(2, 1)
    return x_ellipse, y_ellipse

In [27]:
import matplotlib.animation
import matplotlib.pyplot as plt
import numpy as np
from IPython.display import HTML

plt.rcParams["animation.html"] = "jshtml"
plt.rcParams['figure.dpi'] = 100  # Reduce DPI for performance
plt.ioff()

fig, ax = plt.subplots()

# Stride for quiver reduction
stride = 1  # Reduce density by plotting every 2nd point
frames = range(0, len(tim_ssh), 1)  # Skip frames for efficiency

def animate(t):
    ax.clear()

    target_time = tim_ssh[t]
    ut, vt = u_ssh[:, :, t], v_ssh[:, :, t]

    # Reduce quiver density
    ax.quiver(lon_ssh[::stride, ::stride], lat_ssh[::stride, ::stride], 
              ut.T[::stride, ::stride], vt.T[::stride, ::stride], 
              width=0.004, scale=10)

    # ESPRA SSH Scatter and Ellipse
    df = df_CE2_ssh_trace[df_CE2_ssh_trace['Time'] == target_time]
    if not df.empty:
        ax.scatter(df['x0'], df['y0'], color='blue', label='ESPRA SSH')
        x_ellipse, y_ellipse = plot_ellipse(df['Q'].iloc[0], (df['x0'].iloc[0], df['y0'].iloc[0]), 0.5)
        ax.plot(x_ellipse, y_ellipse, 'b-')

    # Closest ESPRA OBS Scatter and Ellipse
    closest_row = df_CE2_espra.loc[(df_CE2_espra['Time'] - target_time).abs().idxmin()]
    if not closest_row.empty:
        ax.scatter(closest_row['x0'], closest_row['y0'], color='red', label='ESPRA OBS')
        x_ellipse, y_ellipse = plot_ellipse(closest_row['Q'], (closest_row['x0'], closest_row['y0']), 0.5)
        ax.plot(x_ellipse, y_ellipse, 'r-')

    t1 = target_time - pd.Timedelta(days=0.5)
    t2 = target_time + pd.Timedelta(days=0.5)
    time_frame_data = df_CE2_analysis[(df_CE2_analysis['Time'] >= t1) & (df_CE2_analysis['Time'] <= t2)]
    if not time_frame_data.empty:
        ax.scatter(time_frame_data['Lon'], time_frame_data['Lat'], marker='x', color='m')
    
    ax.set_title(f'Time: {target_time}')
    ax.axis('equal')
    ax.set_xlim(lon_min_CE2, lon_max_CE2)
    ax.set_ylim(lat_min_CE2, lat_max_CE2)
    ax.legend(loc='upper right')

# Create animation
ani = matplotlib.animation.FuncAnimation(fig, animate, frames=frames, interval=200)

# Display animation in Jupyter Notebook
HTML(ani.to_jshtml())

